# Introduction to Visualization

In the previous step of the tutorial we made some plots using `hvplot`, which provides interactive plots using a syntax similar to the Pandas `.plot()` method. In addition to Pandas, `hvPlot` supports XArray, Dask, GeoPandas, and a variety of other libraries. The result of an `hvplot` call is a `holoviews` object. This might seem a little mysterious, so we'll take a minute to show how this works. In this tutorial step we'll use generated data for simplicity.

In [1]:
import numpy as np
import pandas as pd

index = pd.date_range('1/1/2000', periods=1000)
df = pd.DataFrame(np.random.randn(1000, 4), index=index, columns=list('ABCD')).cumsum()

df.head()

A         B         C         D
2000-01-01 -0.176015 -0.199271 -0.624194 -1.305688
2000-01-02  0.044903 -0.971680 -0.050065 -1.302616
2000-01-03 -0.255029 -2.196338  0.369382 -3.691017
2000-01-04  0.122579 -0.548694 -0.321886 -3.211658
2000-01-05  1.316440 -1.852900  0.524548 -2.146707

Use `hvplot` to product an interactively explorable plot with panning, zooming, hovering, and clickable/selectable legends:

In [2]:
import hvplot.pandas

df.hvplot()

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [3]:
# Exercise: Scroll in and out of the plot, click on an item in the legend, save a png

## Selection

To inspect this plot more closely we can assign it to a variable and print that variable. We'll see that we in fact have a holoviews object of type `NdOverlay` and subtype `Curve`. 

In [4]:
plot = df.hvplot()
print(plot)

:NdOverlay   [Variable]
   :Curve   [index]   (value)


But what does that mean? What we got out of hvplot was actually a mapping. 

In [5]:
# Exercise: Use plot.keys() to inspect the keys of the mapping.

We can select just one of the variables from the mapping just like you would from a dictionary:

In [6]:
plot['A']

:Curve   [index]   (value)

In [7]:
# Exercise: select a different label from the plot.

We can create an overlay of just a few of the plots using the `*` operator

In [8]:
plot['B'] * plot['C']

:Overlay
   .Curve.I  :Curve   [index]   (value)
   .Curve.II :Curve   [index]   (value)

## Subplots

We can also switch it around so that instead of having all the plots overlayed, we can display them next to each other. For this we will use the '+' operator. Not the we also specified that there should only be one column, otherwise they would be added row-wise. 

In [9]:
(plot['B'] + plot['C']).cols(1)

:Layout
   .Curve.I  :Curve   [index]   (value)
   .Curve.II :Curve   [index]   (value)

Another way to achieve a similar result is to use the `subplots` keyword argument in `hvplot`. 

In [10]:
df.hvplot(subplots=True, width=300).cols(2)

:NdLayout   [Variable]
   :Curve   [index]   (value)

In [11]:
# Exercise: Try to create something other than a line plot. Perhaps a scatter - df.hvplot.scatter(). 
# Challenge: Use tab completion to explore other plot types.

# Visualizing images

In the [Data Ingestion](01_Data_Ingestion.ipynb) tutorial, we saw how you can view Landsat imagery loaded with intake. First let us import `intake` and `hvplot.xarray` to load `hvplot` support for `xarray`:

In [12]:
import intake
import hvplot.xarray

Now we can open the catalog and read in our data for Landsat 5 and 8:

In [13]:
cat = intake.open_catalog('../catalog.yml')
l5 = cat.l5.read_chunked()
l8 = cat.l8.read_chunked()

Using `geo=True` in `hvplot`, we can ensure the appropriate coordinate reference system is used. In the next cell, we use this along with `cmap='fire'` to change the color map:

In [14]:
l5.hvplot(x='x', y='y', datashade=True, geo=True, width=400, cmap='fire')

:DynamicMap   [band]
   :RGB   [x,y]   (R,G,B,A)

In [15]:
# Exercise: Try adjusting the width and adding a height option to make the overall plot bigger or smaller.

The 'fire' colormap is one of the [*perceptually uniform colormaps*](https://arxiv.org/abs/1509.03700) provided by [colorcet](http://colorcet.pyviz.org/). These colormaps are especially designed to help reveal features of the data that may be lost when using colormaps that are not perceptually uniform.

## Combining images with `+`

In the same way you can combine curves with `+` (as shown above using data loaded from a pandas DataFrame), you can do the same using images created with `hvplot`.

In the next cell, we use different colormaps for the  Landsat 5 and Landsat 8 data, datashade them and position them next to each other:

In [16]:
l5plot = l5.hvplot(x='x', y='y', datashade=True, width=400, geo=True, cmap='Reds')
l8plot = l8.hvplot(x='x', y='y', datashade=True, width=400, geo=True, cmap='Blues')
l5plot + l8plot

:Layout
   .DynamicMap.I  :DynamicMap   [band]
      :RGB   [x,y]   (R,G,B,A)
   .DynamicMap.II :DynamicMap   [band]
      :RGB   [x,y]   (R,G,B,A)

As `datashader=True`, the plots refresh with the available data when the zoom tool is used. Note that the plots have linked axes making comparison between plots easier. Note that the plots will only update to show higher resolution if a live Python process is running; on a web site zooming will only ever show the original set of pixels, getting larger on a zoom rather than revealing more data as you'll see if Python is available.

hvPlot also supports a large range of plot types and options not shown here. A more detailed description of visualization options will follow in the [Data Visualization](06_Data_Visualization.ipynb) tutorial. See the [hvplot.pyviz.org](https://hvplot.pyviz.org) website for further details, and [holoviews.org](http://holoviews.org), [geoviews.org](http://geoviews.org), and [datashader.org](http://datashader.org) for information about the underlying functionality and advanced usage. You can also work through the extensive tutorials at [pyviz.org](http://pyviz.org)